In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "slot"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev5"
args.n_epochs = 12000 
args.init_model = "{}-baseline1".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 3001
args.conn_lambda_epochs_end = 8000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 3001
args.valency_lambda_epochs_end = 8000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 3001
args.euler_lambda_epochs_end = 8000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 8000

args.cross_att_use = False
args.cross_att_random = False
args.cross_att_n_sinkhorn = 1
args.cross_att_use_gcn2 = True
args.cross_att_sigmoid = False
args.ot_lambda = -0.1
# args.morgan_bits = 1024

# args.fgw_no_bonds = False

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=8000, conn_lambda_epochs_start=3001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=1, cross_att_random=False, cross_att_sigmoid=False, cross_att_use=False, cross_att_use_gcn2=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=8000, euler_lambda_epochs_start=3001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', fgw_atoms=True, fgw_bonds=True, init_decoder_model='slot-baseline1_decode', init_model='slot-baseline1', linear_out=False, max_num_atoms=70, model_type='slot', morgan_bits=0, n_epochs=12000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [ ]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

No model slot-baseline1 found in mol_opt/output_dev5/slot-baseline1! Starting from scratch.
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=-1 mode=[0 0 0] conn=True val=True euler=True
Epoch: 1


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:3.5397986
 conn_penalty:0.0000000
 val_penalty:624.2515234
 euler_penalty:193.7891016
 total:4.3564816
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 1, train
 fgw:3.5397986
 conn_penalty:0.0000000
 val_penalty:624.2515234
 euler_penalty:193.7891016
 total:4.3564816
Epoch duration: 4.127974987030029
Epoch: 2
Losses Batch 0, train
 fgw:2.6474011
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:2.6474011
Penalty params: tau=0.99942 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=2 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99942 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=2 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 2, train
 fgw:2.6474011
 conn_penalty:0.0000000
 v

Losses Batch 0, train
 fgw:0.7785114
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.7785114
Penalty params: tau=0.99140 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=16 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99140 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=16 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 16, train
 fgw:0.7785114
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.7785114
Epoch duration: 1.1548821926116943
Epoch: 17
Losses Batch 0, train
 fgw:0.7713063
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.7713063
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=17 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=17 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 17, train
 fgw:0.7713063
 conn_penalty:0.0000000
 v

Losses Batch 0, train
 fgw:0.6570230
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.6570230
Penalty params: tau=0.98288 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=31 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.98288 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=31 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 31, train
 fgw:0.6570230
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.6570230
Epoch duration: 1.1018238067626953
Epoch: 32
Losses Batch 0, train
 fgw:0.6381192
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.6381192
Penalty params: tau=0.98231 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=32 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.98231 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=32 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 32, train
 fgw:0.6381192
 conn_penalty:0.0000000
 v

...

Losses Batch 0, train
 fgw:1.0955842
 conn_penalty:0.0869984
 val_penalty:6.3696442
 euler_penalty:10.3410242
 total:11.5637292
Penalty params: tau=0.01772 conn_l=0.61135 val_l=0.92058 euler_l=0.44176 epoch=7006 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01772 conn_l=0.61135 val_l=0.92058 euler_l=0.44176 epoch=7006 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7006, train
 fgw:1.0955842
 conn_penalty:0.0869984
 val_penalty:6.3696442
 euler_penalty:10.3410242
 total:11.5637292
Epoch duration: 5.895307779312134
Epoch: 7007
Losses Batch 0, train
 fgw:1.0809156
 conn_penalty:0.2185863
 val_penalty:9.8281342
 euler_penalty:13.0341907
 total:16.0200525
Penalty params: tau=0.01771 conn_l=0.61233 val_l=0.92215 euler_l=0.44243 epoch=7007 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01771 conn_l=0.61233 val_l=0.92215 euler_l=0.44243 epoch=7007 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7007, train
 fgw:1.0809156
 conn_penalty:0.218

Epoch: 7021
Losses Batch 0, train
 fgw:1.0554235
 conn_penalty:1.1715578
 val_penalty:3.7269370
 euler_penalty:6.0798517
 total:8.0452832
Penalty params: tau=0.01757 conn_l=0.62622 val_l=0.94441 euler_l=0.45195 epoch=7021 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01757 conn_l=0.62622 val_l=0.94441 euler_l=0.45195 epoch=7021 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7021, train
 fgw:1.0554235
 conn_penalty:1.1715578
 val_penalty:3.7269370
 euler_penalty:6.0798517
 total:8.0452832
Epoch duration: 5.211948394775391
Epoch: 7022
Losses Batch 0, train
 fgw:1.0598582
 conn_penalty:0.1598488
 val_penalty:2.0400937
 euler_penalty:5.5880353
 total:5.6121606
Penalty params: tau=0.01756 conn_l=0.62722 val_l=0.94602 euler_l=0.45264 epoch=7022 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01756 conn_l=0.62722 val_l=0.94602 euler_l=0.45264 epoch=7022 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7022, train
 fgw:1.0598582
 conn_penalty

Losses Batch 0, train
 fgw:1.0599628
 conn_penalty:0.5026654
 val_penalty:3.0616690
 euler_penalty:5.6227972
 total:6.9390796
Penalty params: tau=0.01742 conn_l=0.64145 val_l=0.96887 euler_l=0.46238 epoch=7036 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01742 conn_l=0.64145 val_l=0.96887 euler_l=0.46238 epoch=7036 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7036, train
 fgw:1.0599628
 conn_penalty:0.5026654
 val_penalty:3.0616690
 euler_penalty:5.6227972
 total:6.9390796
Epoch duration: 4.409653186798096
Epoch: 7037
Losses Batch 0, train
 fgw:1.0922677
 conn_penalty:0.0095447
 val_penalty:2.1905362
 euler_penalty:5.4206671
 total:5.7271216
Penalty params: tau=0.01741 conn_l=0.64247 val_l=0.97052 euler_l=0.46308 epoch=7037 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01741 conn_l=0.64247 val_l=0.97052 euler_l=0.46308 epoch=7037 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7037, train
 fgw:1.0922677
 conn_penalty:0.0095447
 

Losses Batch 0, train
 fgw:1.1021181
 conn_penalty:0.4064280
 val_penalty:2.9158081
 euler_penalty:5.3060138
 total:6.7681451
Penalty params: tau=0.01727 conn_l=0.65705 val_l=0.99395 euler_l=0.47305 epoch=7051 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01727 conn_l=0.65705 val_l=0.99395 euler_l=0.47305 epoch=7051 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7051, train
 fgw:1.1021181
 conn_penalty:0.4064280
 val_penalty:2.9158081
 euler_penalty:5.3060138
 total:6.7681451
Epoch duration: 5.125285863876343
Epoch: 7052
Losses Batch 0, train
 fgw:1.1174460
 conn_penalty:0.8729280
 val_penalty:2.3572086
 euler_penalty:6.3223260
 total:7.0247046
Penalty params: tau=0.01726 conn_l=0.65810 val_l=0.99565 euler_l=0.47377 epoch=7052 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01726 conn_l=0.65810 val_l=0.99565 euler_l=0.47377 epoch=7052 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7052, train
 fgw:1.1174460
 conn_penalty:0.8729280
 

Losses Batch 0, train
 fgw:1.0932009
 conn_penalty:0.0000000
 val_penalty:2.9298788
 euler_penalty:10.1481915
 total:8.9795435
Penalty params: tau=0.01712 conn_l=0.67302 val_l=1.01968 euler_l=0.48396 epoch=7066 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01712 conn_l=0.67302 val_l=1.01968 euler_l=0.48396 epoch=7066 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7066, train
 fgw:1.0932009
 conn_penalty:0.0000000
 val_penalty:2.9298788
 euler_penalty:10.1481915
 total:8.9795435
Epoch duration: 3.1530582904815674
Epoch: 7067
Losses Batch 0, train
 fgw:1.0845976
 conn_penalty:0.9940213
 val_penalty:3.8243246
 euler_penalty:6.5858905
 total:8.8405255
Penalty params: tau=0.01711 conn_l=0.67410 val_l=1.02142 euler_l=0.48470 epoch=7067 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01711 conn_l=0.67410 val_l=1.02142 euler_l=0.48470 epoch=7067 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7067, train
 fgw:1.0845976
 conn_penalty:0.994021